# Tensor Flow Notebook
## W207 Final Project
### T. P. Goter
### July 6, 2019

This workbook is used to create, fit and analyze various neural networks for facial keypoint detection.

In [ ]:
# Import needed packages
from __future__ import absolute_import, division, print_function, unicode_literals
import tensorflow as tf
import pandas as pd
import numpy as np
import time
from tensorflow.keras import models, layers, callbacks
from tensorflow.keras import optimizers, metrics
from matplotlib import pyplot as plt
%matplotlib inline

In [ ]:
tf.__version__

## Data Loading

- Load in the pickle file that was created as part of the EDA in DataExploration.ipynb. 
- This dataset has the NaNs removed and a few mislabeled images removed as well. 
- As such there is only limited training and development data to use. 
- The image data has already been normalized to [0,1]

In [ ]:
# Initialize Random Seed for reproducibility
np.random.seed(13)

# Load the dataframe from the pickle file
df_nostache_nonan = pd.read_pickle("df_nostache_nonan.pkl")

# Grab the last column - that is our image data for X matrix
X = df_nostache_nonan.iloc[:, -1]

# Convert from a series of arrays to an NDarray
X = np.array([x for x in X])

# Grab the keypoints and stick into our y-variable
y = np.array(df_nostache_nonan.iloc[:,:-1])


## Baseline Neural Net
CNNs are combinations of convolution layers, pooling layers and dropout layers followed by one or two fully connected layers once the number of dimensions has been sufficiently reduced.

1. Let's include just one hidden layer and one output layer
2. The input layer will reduce our flattened 96x96 matrix (i.e., 9216 in length) to a predetermined number of hidden units
3. We will then run sensitivities to # of hidden units, activation, optimizer, and learning rate
4. We will judge our model based on RMSE error and run time.

In [ ]:
def base_model(hidden_units=100, activation='relu'):
    base_model = models.Sequential()
    base_model.add(layers.Dense(hidden_units,activation=activation, kernel_initializer='normal',input_shape=[9216]))
    base_model.add(layers.Dense(30, activation=activation))
    base_model.build()
    print(base_model.summary())
    return base_model
   
class TimeHistory(callbacks.Callback):
    def on_train_begin(self, logs={}):
        self.times = []

    def on_epoch_begin(self, batch, logs={}):
        self.epoch_time_start = time.time()

    def on_epoch_end(self, batch, logs={}):
        self.times.append(time.time() - self.epoch_time_start)

#### Define our optimizers for our initial study

In [19]:
adam = optimizers.Adam(lr=0.001, beta_1=0.9, beta_2=0.999)
sgd = optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=True)
nadam = optimizers.Nadam(lr=0.002, beta_1=0.9, beta_2=0.999, epsilon=None, schedule_decay=0.004)
adagrad = optimizers.Adagrad(lr=0.01, epsilon=None, decay=0.0)

opt_list = {'adam':adam, 'sgd':sgd, 'nadam':nadam, 'adagrad':adagrad}

#### Set up our first DOE

In [66]:
single_layer_base_df = pd.DataFrame()
for hidden_unit in [50, 100, 150, 200]:
    for act in ['relu', 'sigmoid', 'tanh']:
        for opt_name, opt in opt_list.items():
            model = base_model(hidden_units=hidden_unit, activation=act)
            model.compile(optimizer=opt,
                          loss='mean_squared_error',
                          metrics=['mean_squared_error'])
            time_callback = TimeHistory()
            history = model.fit(X, y, epochs=400, validation_split=0.15, callbacks=[time_callback])
            times = time_callback.times

            # Convert to dataframe
            hist = pd.DataFrame(history.history)
            hist['epoch'] = history.epoch
            hist['RMSE'] = np.sqrt(hist.mean_squared_error)
            hist['val_RMSE'] = np.sqrt(hist.val_mean_squared_error)
            hist['times'] = times
            hist['hunits'] = hidden_unit
            hist['activation'] = act
            hist['optimizer'] = opt_name
            hist['lrate'] = opt.get_config()['learning_rate']

            # Keep concatenating to dataframe
            single_layer_base_df = pd.concat([single_layer_base_df,hist])
            
            # Re-pickle after every model to retain progress
            single_layer_base_df.to_pickle("OutputData/single_layer_df.pkl")

            # Save models.
            filename = "base_model_{}_{}_{}".format(hidden_unit, act, opt_name)
            model.save("Models/"+filename+".h5")


Model: "sequential_66"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_132 (Dense)            (None, 50)                460850    
_________________________________________________________________
dense_133 (Dense)            (None, 30)                1530      
Total params: 462,380
Trainable params: 462,380
Non-trainable params: 0
_________________________________________________________________
None
Train on 1819 samples, validate on 321 samples
Epoch 1/400
1819/1819 [==============================] - 0s 191us/sample - loss: 855.1641 - mean_squared_error: 855.1642 - val_loss: 659.0494 - val_mean_squared_error: 659.0494
Epoch 2/400
1819/1819 [==============================] - 0s 118us/sample - loss: 650.3790 - mean_squared_error: 650.3790 - val_loss: 647.6724 - val_mean_squared_error: 647.6724
Epoch 3/400
1819/1819 [==============================] - 0s 135us/sample - loss: 639.5403 - mean_square

1819/1819 [==============================] - 0s 118us/sample - loss: 332.9102 - mean_squared_error: 332.9102 - val_loss: 348.5560 - val_mean_squared_error: 348.5560
Epoch 44/400
1819/1819 [==============================] - 0s 117us/sample - loss: 332.2447 - mean_squared_error: 332.2448 - val_loss: 349.3753 - val_mean_squared_error: 349.3753
Epoch 45/400
1819/1819 [==============================] - 0s 117us/sample - loss: 331.0791 - mean_squared_error: 331.0791 - val_loss: 350.5196 - val_mean_squared_error: 350.5196
Epoch 46/400
1819/1819 [==============================] - 0s 118us/sample - loss: 330.4888 - mean_squared_error: 330.4887 - val_loss: 348.0614 - val_mean_squared_error: 348.0614
Epoch 47/400
1819/1819 [==============================] - 0s 132us/sample - loss: 329.2538 - mean_squared_error: 329.2538 - val_loss: 348.2779 - val_mean_squared_error: 348.2779
Epoch 48/400
1819/1819 [==============================] - 0s 122us/sample - loss: 328.9788 - mean_squared_error: 328.9788 -

1819/1819 [==============================] - 0s 121us/sample - loss: 287.0583 - mean_squared_error: 287.0583 - val_loss: 311.3409 - val_mean_squared_error: 311.3409
Epoch 90/400
1819/1819 [==============================] - 0s 117us/sample - loss: 287.0829 - mean_squared_error: 287.0829 - val_loss: 313.5579 - val_mean_squared_error: 313.5580
Epoch 91/400
1819/1819 [==============================] - 0s 115us/sample - loss: 288.1818 - mean_squared_error: 288.1818 - val_loss: 313.2028 - val_mean_squared_error: 313.2028
Epoch 92/400
1819/1819 [==============================] - 0s 117us/sample - loss: 287.0771 - mean_squared_error: 287.0771 - val_loss: 310.0630 - val_mean_squared_error: 310.0630
Epoch 93/400
1819/1819 [==============================] - 0s 121us/sample - loss: 285.2642 - mean_squared_error: 285.2642 - val_loss: 310.3700 - val_mean_squared_error: 310.3700
Epoch 94/400
1819/1819 [==============================] - 0s 116us/sample - loss: 285.3662 - mean_squared_error: 285.3662 -

Epoch 135/400
1819/1819 [==============================] - 0s 119us/sample - loss: 280.3673 - mean_squared_error: 280.3672 - val_loss: 303.9981 - val_mean_squared_error: 303.9981
Epoch 136/400
1819/1819 [==============================] - 0s 115us/sample - loss: 279.1825 - mean_squared_error: 279.1825 - val_loss: 303.9832 - val_mean_squared_error: 303.9832
Epoch 137/400
1819/1819 [==============================] - 0s 133us/sample - loss: 279.6291 - mean_squared_error: 279.6291 - val_loss: 310.6765 - val_mean_squared_error: 310.6765
Epoch 138/400
1819/1819 [==============================] - 0s 125us/sample - loss: 279.3720 - mean_squared_error: 279.3721 - val_loss: 306.2243 - val_mean_squared_error: 306.2243
Epoch 139/400
1819/1819 [==============================] - 0s 125us/sample - loss: 279.2901 - mean_squared_error: 279.2902 - val_loss: 304.9643 - val_mean_squared_error: 304.9642
Epoch 140/400
1819/1819 [==============================] - 0s 124us/sample - loss: 279.5637 - mean_square

Epoch 181/400
1819/1819 [==============================] - 0s 131us/sample - loss: 276.0971 - mean_squared_error: 276.0971 - val_loss: 300.2387 - val_mean_squared_error: 300.2388
Epoch 182/400
1819/1819 [==============================] - 0s 125us/sample - loss: 276.5903 - mean_squared_error: 276.5903 - val_loss: 307.9544 - val_mean_squared_error: 307.9543
Epoch 183/400
1819/1819 [==============================] - 0s 135us/sample - loss: 275.3136 - mean_squared_error: 275.3136 - val_loss: 299.8249 - val_mean_squared_error: 299.8249
Epoch 184/400
1819/1819 [==============================] - 0s 128us/sample - loss: 275.1678 - mean_squared_error: 275.1678 - val_loss: 300.2036 - val_mean_squared_error: 300.2036
Epoch 185/400
1819/1819 [==============================] - 0s 149us/sample - loss: 275.1948 - mean_squared_error: 275.1948 - val_loss: 300.9904 - val_mean_squared_error: 300.9904
Epoch 186/400
1819/1819 [==============================] - 0s 219us/sample - loss: 274.9820 - mean_square

...

Epoch 186/400
1819/1819 [==============================] - 1s 420us/sample - loss: 2525.4120 - mean_squared_error: 2525.4121 - val_loss: 2520.7353 - val_mean_squared_error: 2520.7354
Epoch 187/400
1819/1819 [==============================] - 1s 421us/sample - loss: 2525.4120 - mean_squared_error: 2525.4124 - val_loss: 2520.7353 - val_mean_squared_error: 2520.7351
Epoch 188/400
1819/1819 [==============================] - 1s 417us/sample - loss: 2525.4120 - mean_squared_error: 2525.4124 - val_loss: 2520.7353 - val_mean_squared_error: 2520.7351
Epoch 189/400
1819/1819 [==============================] - 1s 421us/sample - loss: 2525.4120 - mean_squared_error: 2525.4119 - val_loss: 2520.7353 - val_mean_squared_error: 2520.7351
Epoch 190/400
1819/1819 [==============================] - 1s 421us/sample - loss: 2525.4120 - mean_squared_error: 2525.4121 - val_loss: 2520.7353 - val_mean_squared_error: 2520.7354
Epoch 191/400
1819/1819 [==============================] - 1s 417us/sample - loss: 25

Epoch 231/400
1819/1819 [==============================] - 1s 419us/sample - loss: 2525.4118 - mean_squared_error: 2525.4114 - val_loss: 2520.7352 - val_mean_squared_error: 2520.7351
Epoch 232/400
1819/1819 [==============================] - 1s 422us/sample - loss: 2525.4118 - mean_squared_error: 2525.4121 - val_loss: 2520.7351 - val_mean_squared_error: 2520.7351
Epoch 233/400
1819/1819 [==============================] - 1s 422us/sample - loss: 2525.4118 - mean_squared_error: 2525.4114 - val_loss: 2520.7352 - val_mean_squared_error: 2520.7349
Epoch 234/400
1819/1819 [==============================] - 1s 420us/sample - loss: 2525.4118 - mean_squared_error: 2525.4111 - val_loss: 2520.7351 - val_mean_squared_error: 2520.7351
Epoch 235/400
1819/1819 [==============================] - 1s 419us/sample - loss: 2525.4118 - mean_squared_error: 2525.4114 - val_loss: 2520.7351 - val_mean_squared_error: 2520.7351
Epoch 236/400
1819/1819 [==============================] - 1s 422us/sample - loss: 25

Epoch 276/400
1819/1819 [==============================] - 1s 421us/sample - loss: 2525.4118 - mean_squared_error: 2525.4119 - val_loss: 2520.7351 - val_mean_squared_error: 2520.7351
Epoch 277/400
1819/1819 [==============================] - 1s 424us/sample - loss: 2525.4118 - mean_squared_error: 2525.4119 - val_loss: 2520.7351 - val_mean_squared_error: 2520.7351
Epoch 278/400
1819/1819 [==============================] - 1s 419us/sample - loss: 2525.4118 - mean_squared_error: 2525.4114 - val_loss: 2520.7351 - val_mean_squared_error: 2520.7351
Epoch 279/400
1819/1819 [==============================] - 1s 418us/sample - loss: 2525.4118 - mean_squared_error: 2525.4121 - val_loss: 2520.7351 - val_mean_squared_error: 2520.7351
Epoch 280/400
1819/1819 [==============================] - 1s 421us/sample - loss: 2525.4118 - mean_squared_error: 2525.4119 - val_loss: 2520.7352 - val_mean_squared_error: 2520.7351
Epoch 281/400
1819/1819 [==============================] - 1s 420us/sample - loss: 25

Epoch 321/400
1819/1819 [==============================] - 1s 418us/sample - loss: 2525.4118 - mean_squared_error: 2525.4119 - val_loss: 2520.7352 - val_mean_squared_error: 2520.7351
Epoch 322/400
1819/1819 [==============================] - 1s 421us/sample - loss: 2525.4118 - mean_squared_error: 2525.4121 - val_loss: 2520.7351 - val_mean_squared_error: 2520.7351
Epoch 323/400
1819/1819 [==============================] - 1s 420us/sample - loss: 2525.4118 - mean_squared_error: 2525.4124 - val_loss: 2520.7351 - val_mean_squared_error: 2520.7351
Epoch 324/400
1819/1819 [==============================] - 1s 418us/sample - loss: 2525.4118 - mean_squared_error: 2525.4114 - val_loss: 2520.7351 - val_mean_squared_error: 2520.7351
Epoch 325/400
1819/1819 [==============================] - 1s 429us/sample - loss: 2525.4118 - mean_squared_error: 2525.4119 - val_loss: 2520.7352 - val_mean_squared_error: 2520.7351
Epoch 326/400
1819/1819 [==============================] - 1s 424us/sample - loss: 25

Epoch 366/400
1819/1819 [==============================] - 1s 429us/sample - loss: 2525.4118 - mean_squared_error: 2525.4121 - val_loss: 2520.7351 - val_mean_squared_error: 2520.7351
Epoch 367/400
1819/1819 [==============================] - 1s 444us/sample - loss: 2525.4118 - mean_squared_error: 2525.4121 - val_loss: 2520.7351 - val_mean_squared_error: 2520.7351
Epoch 368/400
1819/1819 [==============================] - 1s 423us/sample - loss: 2525.4118 - mean_squared_error: 2525.4119 - val_loss: 2520.7351 - val_mean_squared_error: 2520.7351
Epoch 369/400
1819/1819 [==============================] - 1s 422us/sample - loss: 2525.4118 - mean_squared_error: 2525.4124 - val_loss: 2520.7351 - val_mean_squared_error: 2520.7349
Epoch 370/400
1819/1819 [==============================] - 1s 418us/sample - loss: 2525.4118 - mean_squared_error: 2525.4114 - val_loss: 2520.7351 - val_mean_squared_error: 2520.7351
Epoch 371/400
1819/1819 [==============================] - 1s 420us/sample - loss: 25

## Plot Some of the Baseline Model Results

In [68]:
single_layer_base_df.sample(10)

loss  mean_squared_error     val_loss  val_mean_squared_error  \
141  2525.412542         2525.412109  2520.735898             2520.735840   
51   2525.411773         2525.411865  2520.735137             2520.735107   
171   774.282031          774.282227   788.253403              788.253357   
62    290.515870          290.515869   315.225821              315.225800   
53   2525.411869         2525.412109  2520.735175             2520.735107   
270  2525.411525         2525.411377  2520.734837             2520.735107   
350  2408.650358         2408.650391  2403.430776             2403.430664   
121   156.017402          156.017410   185.425430              185.425430   
95   2525.411992         2525.412842  2520.735322             2520.735596   
115  2525.414910         2525.415039  2520.738238             2520.738281   

     epoch       RMSE   val_RMSE     times  hunits activation optimizer  lrate  
141    141  50.253479  50.206930  0.223230      50    sigmoid       sgd  0.010  
51      51  50.253476  50.206923  0.339097     100       tanh      adam  0.001  
171    171  27.825927  28.075850  1.317899     200       relu     nadam  0.002  
62      62  17.044526  17.754599  0.317279     100       relu      adam  0.001  
53      53  50.253479  50.206923  1.055051     150    sigmoid     nadam  0.002  
270    270  50.253471  50.206923  1.337592     200    sigmoid     nadam  0.002  
350    350  49.078003  49.024796  0.406882     150       relu       sgd  0.010  
121    121  12.490693  13.617101  0.738630     100       relu     nadam  0.002  
95      95  50.253486  50.206928  0.198743      50       tanh      adam  0.001  
115    115  50.253508  50.206955  0.622873     150    sigmoid   adagrad  0.010

### Softmax + Base DOE

In [ ]:
def softmax_model(hidden_units=100, activation='relu'):
    softmax_model = models.Sequential()
    softmax_model.add(layers.Dense(hidden_units,activation=activation, kernel_initializer='normal',input_shape=[9216]))
    softmax_model.add(layers.Dense(30, activation='softmax'))
    softmax_model.build()
    print(softmax_model.summary())
    return softmax_model


single_layer_softmax_df = pd.DataFrame()
for hidden_unit in [50, 100, 150, 200]:
    for act in ['relu', 'sigmoid', 'tanh']:
        for opt_name, opt in opt_list.items():
            model = softmax_model(hidden_units=hidden_unit, activation=act)
            model.compile(optimizer=opt,
                          loss='mean_squared_error',
                          metrics=['mean_squared_error'])
            time_callback = TimeHistory()
            history = model.fit(X, y, epochs=400, validation_split=0.15, callbacks=[time_callback])
            times = time_callback.times

            # Convert to dataframe
            hist = pd.DataFrame(history.history)
            hist['epoch'] = history.epoch
            hist['RMSE'] = np.sqrt(hist.mean_squared_error)
            hist['val_RMSE'] = np.sqrt(hist.val_mean_squared_error)
            hist['times'] = times
            hist['hunits'] = hidden_unit
            hist['activation'] = act
            hist['optimizer'] = opt_name
            hist['lrate'] = opt.get_config()['learning_rate']

            # Keep concatenating to dataframe
            single_layer_softmax_df = pd.concat([single_layer_softmax_df,hist])
            
            # Re-pickle after every model to retain progress
            single_layer_softmax_df.to_pickle("OutputData/single_layer_softmax_df.pkl")

            # Save models.
            filename = "base_model_{}_{}_{}".format(hidden_unit, act, opt_name)
            model.save("Models/"+filename+".h5")


Model: "sequential_114"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_228 (Dense)            (None, 50)                460850    
_________________________________________________________________
dense_229 (Dense)            (None, 30)                1530      
Total params: 462,380
Trainable params: 462,380
Non-trainable params: 0
_________________________________________________________________
None
Train on 1819 samples, validate on 321 samples
Epoch 1/400
1819/1819 [==============================] - 1s 545us/sample - loss: 2615.2150 - mean_squared_error: 2615.2148 - val_loss: 2610.4940 - val_mean_squared_error: 2610.4937
Epoch 2/400
1819/1819 [==============================] - 0s 116us/sample - loss: 2615.2069 - mean_squared_error: 2615.2065 - val_loss: 2610.4941 - val_mean_squared_error: 2610.4941
Epoch 3/400
1819/1819 [==============================] - 0s 121us/sample - loss: 2615.2069 - m

1819/1819 [==============================] - 0s 111us/sample - loss: 2615.2069 - mean_squared_error: 2615.2070 - val_loss: 2610.4940 - val_mean_squared_error: 2610.4941
Epoch 43/400
1819/1819 [==============================] - 0s 120us/sample - loss: 2615.2069 - mean_squared_error: 2615.2073 - val_loss: 2610.4939 - val_mean_squared_error: 2610.4937
Epoch 44/400
1819/1819 [==============================] - 0s 122us/sample - loss: 2615.2069 - mean_squared_error: 2615.2065 - val_loss: 2610.4940 - val_mean_squared_error: 2610.4941
Epoch 45/400
1819/1819 [==============================] - 0s 120us/sample - loss: 2615.2069 - mean_squared_error: 2615.2070 - val_loss: 2610.4940 - val_mean_squared_error: 2610.4941
Epoch 46/400
1819/1819 [==============================] - 0s 120us/sample - loss: 2615.2069 - mean_squared_error: 2615.2070 - val_loss: 2610.4941 - val_mean_squared_error: 2610.4939
Epoch 47/400
1819/1819 [==============================] - 0s 124us/sample - loss: 2615.2069 - mean_squa

1819/1819 [==============================] - 0s 114us/sample - loss: 2615.2069 - mean_squared_error: 2615.2070 - val_loss: 2610.4940 - val_mean_squared_error: 2610.4939
Epoch 88/400
1819/1819 [==============================] - 0s 112us/sample - loss: 2615.2069 - mean_squared_error: 2615.2070 - val_loss: 2610.4940 - val_mean_squared_error: 2610.4939
Epoch 89/400
1819/1819 [==============================] - 0s 111us/sample - loss: 2615.2069 - mean_squared_error: 2615.2075 - val_loss: 2610.4940 - val_mean_squared_error: 2610.4941
Epoch 90/400
1819/1819 [==============================] - 0s 111us/sample - loss: 2615.2069 - mean_squared_error: 2615.2065 - val_loss: 2610.4940 - val_mean_squared_error: 2610.4941
Epoch 91/400
1819/1819 [==============================] - 0s 111us/sample - loss: 2615.2069 - mean_squared_error: 2615.2068 - val_loss: 2610.4940 - val_mean_squared_error: 2610.4939
Epoch 92/400
1819/1819 [==============================] - 0s 110us/sample - loss: 2615.2069 - mean_squa

Epoch 132/400
1819/1819 [==============================] - 0s 112us/sample - loss: 2615.2069 - mean_squared_error: 2615.2068 - val_loss: 2610.4940 - val_mean_squared_error: 2610.4937
Epoch 133/400
1819/1819 [==============================] - 0s 113us/sample - loss: 2615.2069 - mean_squared_error: 2615.2070 - val_loss: 2610.4940 - val_mean_squared_error: 2610.4941
Epoch 134/400
1819/1819 [==============================] - 0s 112us/sample - loss: 2615.2069 - mean_squared_error: 2615.2068 - val_loss: 2610.4940 - val_mean_squared_error: 2610.4939
Epoch 135/400
1819/1819 [==============================] - 0s 110us/sample - loss: 2615.2069 - mean_squared_error: 2615.2068 - val_loss: 2610.4940 - val_mean_squared_error: 2610.4939
Epoch 136/400
1819/1819 [==============================] - 0s 110us/sample - loss: 2615.2069 - mean_squared_error: 2615.2068 - val_loss: 2610.4940 - val_mean_squared_error: 2610.4941
Epoch 137/400
1819/1819 [==============================] - 0s 114us/sample - loss: 26

Epoch 177/400
1819/1819 [==============================] - 0s 114us/sample - loss: 2615.2069 - mean_squared_error: 2615.2070 - val_loss: 2610.4941 - val_mean_squared_error: 2610.4941
Epoch 178/400
1819/1819 [==============================] - 0s 112us/sample - loss: 2615.2069 - mean_squared_error: 2615.2065 - val_loss: 2610.4940 - val_mean_squared_error: 2610.4937
Epoch 179/400
1819/1819 [==============================] - 0s 112us/sample - loss: 2615.2069 - mean_squared_error: 2615.2073 - val_loss: 2610.4940 - val_mean_squared_error: 2610.4941
Epoch 180/400
1819/1819 [==============================] - 0s 113us/sample - loss: 2615.2069 - mean_squared_error: 2615.2073 - val_loss: 2610.4941 - val_mean_squared_error: 2610.4941
Epoch 181/400
1819/1819 [==============================] - 0s 111us/sample - loss: 2615.2069 - mean_squared_error: 2615.2070 - val_loss: 2610.4940 - val_mean_squared_error: 2610.4941
Epoch 182/400
1819/1819 [==============================] - 0s 111us/sample - loss: 26

...

Epoch 309/400
1819/1819 [==============================] - 1s 728us/sample - loss: 2614.1131 - mean_squared_error: 2614.1128 - val_loss: 2609.3991 - val_mean_squared_error: 2609.3992
Epoch 310/400
1819/1819 [==============================] - 1s 716us/sample - loss: 2614.1131 - mean_squared_error: 2614.1133 - val_loss: 2609.3991 - val_mean_squared_error: 2609.3989
Epoch 311/400
1819/1819 [==============================] - 1s 716us/sample - loss: 2614.1131 - mean_squared_error: 2614.1130 - val_loss: 2609.3991 - val_mean_squared_error: 2609.3987
Epoch 312/400
1819/1819 [==============================] - 1s 712us/sample - loss: 2614.1132 - mean_squared_error: 2614.1130 - val_loss: 2609.3991 - val_mean_squared_error: 2609.3992
Epoch 313/400
1819/1819 [==============================] - 1s 710us/sample - loss: 2614.1131 - mean_squared_error: 2614.1133 - val_loss: 2609.3991 - val_mean_squared_error: 2609.3994
Epoch 314/400
1819/1819 [==============================] - 1s 713us/sample - loss: 26

Epoch 354/400
1819/1819 [==============================] - 1s 694us/sample - loss: 2614.1131 - mean_squared_error: 2614.1130 - val_loss: 2609.3991 - val_mean_squared_error: 2609.3994
Epoch 355/400
1819/1819 [==============================] - 1s 691us/sample - loss: 2614.1131 - mean_squared_error: 2614.1128 - val_loss: 2609.3991 - val_mean_squared_error: 2609.3992
Epoch 356/400
1819/1819 [==============================] - 1s 685us/sample - loss: 2614.1132 - mean_squared_error: 2614.1128 - val_loss: 2609.3992 - val_mean_squared_error: 2609.3994
Epoch 357/400
1819/1819 [==============================] - 1s 683us/sample - loss: 2614.1131 - mean_squared_error: 2614.1130 - val_loss: 2609.3991 - val_mean_squared_error: 2609.3989
Epoch 358/400
1819/1819 [==============================] - 1s 695us/sample - loss: 2614.1131 - mean_squared_error: 2614.1130 - val_loss: 2609.3991 - val_mean_squared_error: 2609.3992
Epoch 359/400
1819/1819 [==============================] - 1s 687us/sample - loss: 26

Epoch 399/400
1819/1819 [==============================] - 1s 685us/sample - loss: 2614.1131 - mean_squared_error: 2614.1133 - val_loss: 2609.3991 - val_mean_squared_error: 2609.3992
Epoch 400/400
1819/1819 [==============================] - 1s 694us/sample - loss: 2614.1131 - mean_squared_error: 2614.1138 - val_loss: 2609.3991 - val_mean_squared_error: 2609.3989
Model: "sequential_161"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_322 (Dense)            (None, 200)               1843400   
_________________________________________________________________
dense_323 (Dense)            (None, 30)                6030      
Total params: 1,849,430
Trainable params: 1,849,430
Non-trainable params: 0
_________________________________________________________________
None
Train on 1819 samples, validate on 321 samples
Epoch 1/400
1819/1819 [==============================] - 1s 512us/sample - loss: 2614.

1819/1819 [==============================] - 1s 427us/sample - loss: 2614.1132 - mean_squared_error: 2614.1130 - val_loss: 2609.3992 - val_mean_squared_error: 2609.3992
Epoch 41/400
1819/1819 [==============================] - 1s 426us/sample - loss: 2614.1132 - mean_squared_error: 2614.1133 - val_loss: 2609.3992 - val_mean_squared_error: 2609.3992
Epoch 42/400
1819/1819 [==============================] - 1s 427us/sample - loss: 2614.1132 - mean_squared_error: 2614.1135 - val_loss: 2609.3993 - val_mean_squared_error: 2609.3994
Epoch 43/400
1819/1819 [==============================] - 1s 429us/sample - loss: 2614.1132 - mean_squared_error: 2614.1135 - val_loss: 2609.3992 - val_mean_squared_error: 2609.3992
Epoch 44/400
1819/1819 [==============================] - 1s 433us/sample - loss: 2614.1132 - mean_squared_error: 2614.1135 - val_loss: 2609.3992 - val_mean_squared_error: 2609.3992
Epoch 45/400
1819/1819 [==============================] - 1s 439us/sample - loss: 2614.1132 - mean_squa

1819/1819 [==============================] - 1s 446us/sample - loss: 2614.1132 - mean_squared_error: 2614.1130 - val_loss: 2609.3992 - val_mean_squared_error: 2609.3994
Epoch 86/400
1819/1819 [==============================] - 1s 448us/sample - loss: 2614.1131 - mean_squared_error: 2614.1128 - val_loss: 2609.3992 - val_mean_squared_error: 2609.3994
Epoch 87/400
1819/1819 [==============================] - 1s 447us/sample - loss: 2614.1132 - mean_squared_error: 2614.1130 - val_loss: 2609.3992 - val_mean_squared_error: 2609.3989
Epoch 88/400
1819/1819 [==============================] - 1s 425us/sample - loss: 2614.1132 - mean_squared_error: 2614.1135 - val_loss: 2609.3992 - val_mean_squared_error: 2609.3989
Epoch 89/400
1819/1819 [==============================] - 1s 424us/sample - loss: 2614.1132 - mean_squared_error: 2614.1133 - val_loss: 2609.3992 - val_mean_squared_error: 2609.3992
Epoch 90/400
1819/1819 [==============================] - 1s 426us/sample - loss: 2614.1132 - mean_squa

### Parameterize the optimizers and run DOE with 50 and 100 hidden units

We will run one optimizer at a time. For a set of three learning rates.

In [ ]:
# We already have the default learning rate for adam. So let's move up and down to determine accuracy sensitivity
adam_005 = optimizers.Adam(lr=0.005, beta_1=0.9, beta_2=0.999)
adam_0005 = optimizers.Adam(lr=0.0005, beta_1=0.9, beta_2=0.999)

# We already have the default learning rate for adagrad. So let's move up and down to determine accuracy sensitivity
adagrad_02 = optimizers.Adagrad(lr=0.02, epsilon=None, decay=0.0)
adagrad_005 = optimizers.Adagrad(lr=0.05, epsilon=None, decay=0.0)

opt_list_adam = {'adam_005':adam_005, 'adam_0005':adam_0005}
opt_list_nadam = {'nadam_001':nadam_001, 'nadam_01':nadam_01}
opt_list_adagrad = {'adagrad_02':adagrad_02, 'adagrad_005':adagrad_005}

In [ ]:
plot_history(history)

In [ ]:
len(times)

In [ ]:
model.predict(train_X[0:2])